In [0]:
%sql
USE f1_processed;

In [0]:
dbutils.widgets.text("p_file_date","2021-03-21")
v_file_date = dbutils.widgets.get("p_file_date")

In [0]:
spark.sql(f"""
 CREATE TABLE IF NOT EXISTS f1_presentation.calculated_race_results 

(race_year INT,
 team_name STRING,
 driver_id INT,
 driver_name STRING,
 race_id INT,
 position INT,
 points INT,
 calculated_points INT,
 created_date TIMESTAMP,
 updated_date TIMESTAMP
 )
    USING DELTA         
           """)



Out[36]: DataFrame[]

In [0]:
# %sql
# CREATE TABLE IF NOT EXISTS f1_presentation.calculated_race_results 
# USING parquet
# AS
# SELECT races.race_year,
# constructors.name as team_name,
# drivers.name as driver_name,
# results.position,
# results.points,
# 11- results.position AS calculated_points

# FROM results
# JOIN f1_processed.drivers ON ( results.driver_id = drivers.driver_id)
# JOIN f1_processed.constructors ON ( results.constructor_id = constructors.constructor_id)
# JOIN f1_processed.races ON ( results.race_id = races.race_id)
# WHERE results.position <=10

In [0]:
spark.sql (f"""
CREATE OR REPLACE TEMP VIEW race_results_updated
AS
SELECT races.race_year,
constructors.name as team_name,
drivers.driver_id,
drivers.name as driver_name,
races.race_id,
results.position,
results.points,
11- results.position AS calculated_points

FROM f1_processed.results
JOIN f1_processed.drivers ON ( results.driver_id = drivers.driver_id)
JOIN f1_processed.constructors ON ( results.constructor_id = constructors.constructor_id)
JOIN f1_processed.races ON ( results.race_id = races.race_id)
WHERE results.position <=10
AND results.file_date = '{v_file_date}'
""")

Out[38]: DataFrame[]

In [0]:
spark.sql(f"""
MERGE INTO f1_presentation.calculated_race_results tgt
USING race_results_updated upd 
ON (tgt.driver_id = upd.driver_id AND tgt.race_id = upd.race_id)
WHEN MATCHED THEN 
UPDATE SET tgt.position = upd.position ,
tgt.points= upd.points,
tgt.calculated_points= upd.calculated_points,
tgt.updated_date = current_timestamp
WHEN NOT MATCHED 
THEN INSERT 
(race_year, team_name, driver_id, driver_name, race_id, position, points, calculated_points, created_date)
VALUES (race_year, team_name, driver_id, driver_name, race_id, position, points, calculated_points, current_timestamp)
""")

Out[39]: DataFrame[num_affected_rows: bigint, num_updated_rows: bigint, num_deleted_rows: bigint, num_inserted_rows: bigint]

In [0]:
%sql
SELECT * FROM race_results_updated WHERE race_year = 2021

race_year team_name driver_id driver_name race_id position points calculated_points 2021 Mercedes 1 Lewis Hamilton 1053 2 19.0 9 2021 Alpine F1 Team 4 Fernando Alonso 1053 10 1.0 1 2021 AlphaTauri 842 Pierre Gasly 1053 7 6.0 4 2021 McLaren 817 Daniel Ricciardo 1053 6 8.0 5 2021 Red Bull 830 Max Verstappen 1053 1 25.0 10 2021 Ferrari 832 Carlos Sainz 1053 5 10.0 6 2021 Alpine F1 Team 839 Esteban Ocon 1053 9 2.0 2 2021 Aston Martin 840 Lance Stroll 1053 8 4.0 3 2021 Ferrari 844 Charles Leclerc 1053 4 12.0 7 2021 McLaren 846 Lando Norris 1053 3 15.0 8

In [0]:
%sql
SELECT count(1) FROM race_results_updated;

count(1) 10

In [0]:
%sql
SELECT * FROM f1_presentation.calculated_race_results

race_year team_name driver_id driver_name race_id position points calculated_points created_date updated_date 1976 Ligier 172 Jacques Laffite 575 7 0 4 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1976 Surtees 178 Alan Jones 575 4 3 7 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1976 Shadow 197 Jean-Pierre Jarier 575 10 0 1 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1976 Team Lotus 207 Mario Andretti 575 1 9 10 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1976 Tyrrell 221 Patrick Depailler 575 2 6 9 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1976 Ferrari 223 Clay Regazzoni 575 5 2 6 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1976 McLaren 231 James Hunt 575 3 4 8 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1972 Brabham 199 Carlos Reutemann 626 8 0 3 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1972 Team Lotus 224 Emerson Fittipaldi 626 1 9 10 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1972 Matra 278 Chris Amon 626 4 3 7 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1972 McLaren 304 Denny Hulme 626 5 2 6 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1972 McLaren 309 Peter Revson 626 3 4 8 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1987 Team Lotus 102 Ayrton Senna 395 3 4 8 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1987 Larrousse 112 Philippe Alliot 395 6 1 5 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1987 McLaren 117 Alain Prost 395 7 0 4 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1987 McLaren 140 Stefan Johansson 395 2 6 9 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2010 McLaren 1 Lewis Hamilton 346 2 18 9 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2010 Mercedes 3 Nico Rosberg 346 3 15 8 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2010 McLaren 18 Jenson Button 346 4 12 7 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2010 Red Bull 20 Sebastian Vettel 346 7 6 4 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2010 Sauber 155 Kamui Kobayashi 346 6 8 5 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1993 Williams 71 Damon Hill 283 1 10 10 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1993 Ferrari 77 Gerhard Berger 283 3 4 8 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1993 Ligier 84 Martin Brundle 283 5 2 6 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1993 Ligier 87 Mark Blundell 283 7 0 4 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1993 Sauber 91 Karl Wendlinger 283 6 1 5 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1993 Larrousse 112 Philippe Alliot 283 8 0 3 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1993 Jordan 123 Thierry Boutsen 283 9 0 2 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2005 Williams 2 Nick Heidfeld 74 6 3 5 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2005 Renault 4 Fernando Alonso 74 1 10 10 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2005 Sauber 13 Felipe Massa 74 10 0 1 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2005 Toyota 23 Ralf Schumacher 74 9 0 2 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 2005 Red Bull 24 Vitantonio Liuzzi 74 8 1 3 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1975 Ferrari 182 Niki Lauda 584 1 9 10 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1975 Shadow-Ford 197 Jean-Pierre Jarier 584 8 0 3 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1975 Parnelli 207 Mario Andretti 584 5 2 6 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1975 Hesketh 231 James Hunt 584 2 6 9 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1975 Team Lotus 238 Ronnie Peterson 584 10 0 1 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.463+0000 1975 Embassy Hill 294 Tony Brise 584 7 0 4 2025-04-11T00:26:26.120+0000 2025-04-11T00:27:49.4